In [232]:
import pandas as pd
import numpy as np
import joblib


In [191]:
df_train = pd.read_csv('train.tsv', sep='\t', header=None)

In [192]:
pd.set_option('display.max_columns', 500)

In [193]:
df_train.head()

0                1       2                          3     4   \
0  309000.0  do zamieszkania  390 zł  spółdzielcze własnościowe  7113   
1  314900.0   do wykończenia     NaN             pełna własność  7392   
2  249000.0       do remontu  300 zł             pełna własność  5621   
3  419000.0  do zamieszkania  490 zł             pełna własność  4761   
4  499000.0              NaN  850 zł                        NaN  6481   

                                                  5  6   7      8          9   \
0  https://www.otodom.pl/oferta/niezalezny-uklad-...  2 NaN  43.44     wtórny   
1  https://www.otodom.pl/oferta/urokliwe-mieszkan...  2 NaN  42.60  pierwotny   
2  https://www.otodom.pl/oferta/mieszkanie-do-rem...  2 NaN  44.30     wtórny   
3  https://www.otodom.pl/oferta/w-szeregowcu-4-po...  4 NaN     88     wtórny   
4  https://www.otodom.pl/oferta/komfortowe-przest...  3 NaN     77     wtórny   

     10           11  12  13  \
0   4.0         blok NaN NaN   
1   2.0         blok NaN NaN   
2   4.0         blok NaN NaN   
3   3.0  szeregowiec NaN NaN   
4  16.0         blok NaN NaN   

                                                  14 15  16        17  \
0             Niezależny Układ W Nowoczesnym Wydaniu  1 NaN    gazowe   
1           Urokliwe mieszkanie 2 pokojowe Strzeszyn  1 NaN    gazowe   
2  Mieszkanie do remontu ul. Klonowa, blisko tramwaj  2 NaN  miejskie   
3                    W szeregowcu 4 pokoje z garażem  1 NaN    gazowe   
4  Komfortowe,Przestronne,3Pokoje, Armii Krajowej!!!  7 NaN       NaN   

           18      19  20          21     22  \
0  plastikowe     NaN NaN         NaN  cegła   
1  plastikowe     NaN NaN         NaN  cegła   
2  plastikowe  1960.0 NaN  2019-06-30  cegła   
3  plastikowe     NaN NaN         NaN  cegła   
4  plastikowe     NaN NaN         NaN    NaN   

                                                  23  24  \
0   Polecamy na sprzedaż dwupokojowe mieszkanie p... NaN   
1   Kameralne 2 pokojowe mieszkanie z aneksem kuc... NaN   
2   Oferta bezpośrednio od właściciela - bez pośr... NaN   
3   Drodzy Państwo Zapraszam do zapoznania się z ... NaN   
4   Biuro Immohouse ma przyjemność proponować do ... NaN   

                                                  25  
0  telewizja kablowa, internet, meble, piwnica, g...  
1  telewizja kablowa, internet, telefon, drzwi / ...  
2  telewizja kablowa, internet, telefon, domofon ...  
3  telewizja kablowa, internet, zmywarka, lodówka...  
4                             balkon, piwnica, winda

1,2,6, 8, 9 - to bedziemy w aplikacji używać


In [194]:
df_train = df_train.iloc[:, [0, 1, 2, 6, 8, 9]]

In [195]:
df_train.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 2547 entries, 0 to 2546
Data columns (total 6 columns):
 #   Column  Non-Null Count  Dtype  
---  ------  --------------  -----  
 0   0       2547 non-null   float64
 1   1       1519 non-null   object 
 2   2       929 non-null    object 
 3   6       2547 non-null   object 
 4   8       2547 non-null   object 
 5   9       2547 non-null   object 
dtypes: float64(1), object(5)
memory usage: 119.5+ KB


In [196]:
df_train.rename(columns={0: "cena m", 1: "stan", 2: "czynsz", 6: "l pokoi", 8: "metraż", 9: "rynek"}, inplace=True)

In [197]:
df_train.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 2547 entries, 0 to 2546
Data columns (total 6 columns):
 #   Column   Non-Null Count  Dtype  
---  ------   --------------  -----  
 0   cena m   2547 non-null   float64
 1   stan     1519 non-null   object 
 2   czynsz   929 non-null    object 
 3   l pokoi  2547 non-null   object 
 4   metraż   2547 non-null   object 
 5   rynek    2547 non-null   object 
dtypes: float64(1), object(5)
memory usage: 119.5+ KB


Usunięcie kolumn, w których jest dużo pustych wartości

In [198]:
df_train.drop(columns = ['czynsz'], axis=1, inplace=True)

In [199]:
df_train.head()

cena m             stan l pokoi metraż      rynek
0  309000.0  do zamieszkania       2  43.44     wtórny
1  314900.0   do wykończenia       2  42.60  pierwotny
2  249000.0       do remontu       2  44.30     wtórny
3  419000.0  do zamieszkania       4     88     wtórny
4  499000.0              NaN       3     77     wtórny

Uzupełnianie braków w danych 

In [200]:
df_train.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 2547 entries, 0 to 2546
Data columns (total 5 columns):
 #   Column   Non-Null Count  Dtype  
---  ------   --------------  -----  
 0   cena m   2547 non-null   float64
 1   stan     1519 non-null   object 
 2   l pokoi  2547 non-null   object 
 3   metraż   2547 non-null   object 
 4   rynek    2547 non-null   object 
dtypes: float64(1), object(4)
memory usage: 99.6+ KB


In [201]:
df_train['stan'].fillna('brak info', inplace=True)

In [202]:
df_train = df_train[df_train['metraż'] != "6 909"]

In [203]:
df_train = df_train[df_train['l pokoi'] != "więcej niż 10"]

In [204]:
df_train['l pokoi'] = pd.to_numeric(df_train['l pokoi'])

In [205]:
df_train['metraż'] = pd.to_numeric(df_train['metraż'])

In [206]:
X_train = df_train.drop(columns = ["cena m"])
y_train = df_train["cena m"]

In [207]:
number_cols = X_train.select_dtypes(exclude=[object]).columns
object_cols = X_train.select_dtypes(include=[object]).columns

In [208]:
from sklearn.compose import ColumnTransformer
from sklearn.preprocessing import OneHotEncoder
from sklearn.preprocessing import StandardScaler
from sklearn.pipeline import make_pipeline

In [209]:
ct = ColumnTransformer([
        (number_cols, StandardScaler()),
        (object_cols, OneHotEncoder())
    ],remainder='passthrough')


In [210]:
from sklearn.linear_model import Ridge

In [211]:
scaler = StandardScaler()
encoder = OneHotEncoder()
# putting numeric columns to scaler and categorical to encoder
num_transformer = make_pipeline(scaler)
cat_transformer = make_pipeline(encoder)

# getting together our scaler and encoder with preprocessor
preprocessor = ColumnTransformer(
      transformers=[('num', num_transformer, number_cols),
                    ('cat', cat_transformer, object_cols)])

In [212]:
clf = Ridge(alpha=1.0)

In [213]:
model1 = make_pipeline(preprocessor, clf)

In [214]:
X_train.head()

stan  l pokoi  metraż      rynek
0  do zamieszkania        2   43.44     wtórny
1   do wykończenia        2   42.60  pierwotny
2       do remontu        2   44.30     wtórny
3  do zamieszkania        4   88.00     wtórny
4        brak info        3   77.00     wtórny

In [215]:
y_train

0       309000.0
1       314900.0
2       249000.0
3       419000.0
4       499000.0
          ...   
2541    383680.0
2542    507600.0
2543    342400.0
2544    335000.0
2545    260000.0
Name: cena m, Length: 2540, dtype: float64

## Model Ridge - regresja liniowa

In [216]:
model1.fit(X_train, y_train)

Pipeline(steps=[('columntransformer',
                 ColumnTransformer(transformers=[('num',
                                                  Pipeline(steps=[('standardscaler',
                                                                   StandardScaler())]),
                                                  Index(['l pokoi', 'metraż'], dtype='object')),
                                                 ('cat',
                                                  Pipeline(steps=[('onehotencoder',
                                                                   OneHotEncoder())]),
                                                  Index(['stan', 'rynek'], dtype='object'))])),
                ('ridge', Ridge())])

In [217]:
df_test = pd.read_csv('in.tsv', sep='\t', header=None)

In [218]:
df_test.head()

0       1                          2     3   \
0  do zamieszkania  250 zł             pełna własność  6311   
1  do zamieszkania     NaN             pełna własność  7868   
2  do zamieszkania  650 zł             pełna własność  5717   
3  do zamieszkania  359 zł  spółdzielcze własnościowe  7380   
4              NaN     NaN                        NaN  7373   

                                                  4   5   6      7   \
0  https://www.otodom.pl/oferta/idealne-mieszkani...   3 NaN  59.10   
1  https://www.otodom.pl/oferta/2-pokoje-38m2-po-...   2 NaN  38.00   
2  https://www.otodom.pl/oferta/3-pokoje-na-jezyc...   3 NaN  63.84   
3  https://www.otodom.pl/oferta/uniwersytet-przyr...   4 NaN  50.00   
4  https://www.otodom.pl/oferta/mieszkanie-blisko...   3 NaN  65.62   

          8     9     10  11  12  \
0     wtórny   4.0  blok NaN NaN   
1     wtórny  12.0  blok NaN NaN   
2     wtórny   4.0  blok NaN NaN   
3     wtórny  10.0  blok NaN NaN   
4  pierwotny   3.0   NaN NaN NaN   

                                                13  14  15        16  \
0      idealne mieszkanie do zamieszkania od zaraz   2 NaN  miejskie   
1        2 pokoje / 38m2 / po remoncie / Winogrady   4 NaN      inne   
2              3 pokoje na Jeżycach blisko Rusałki   4 NaN  miejskie   
3  Uniwersytet Przyrodniczy - 4 pokoje - ROI 8-10%  10 NaN  miejskie   
4  Mieszkanie blisko centrum w kameralnej okolicy.   1 NaN       NaN   

           17      18  19          20            21  \
0  plastikowe     NaN NaN         NaN  wielka płyta   
1  plastikowe     NaN NaN         NaN           NaN   
2  plastikowe  1958.0 NaN         NaN         cegła   
3  plastikowe  1975.0 NaN  2019-06-30  wielka płyta   
4         NaN  2020.0 NaN  2020-01-01           NaN   

                                                  22  23  \
0   Zamieszkaj od zaraz – idealna lokalizacja OFE... NaN   
1   Na sprzedaż mieszkanie dwupokojowe na osiedlu... NaN   
2   !! Oferta dostępna tylko u nas !! Polecam ofe... NaN   
3   Oferta  bezpośrednio od właściciela  - bez po... NaN   
4   MIESZKANIE 3-POKOJOWE O POW.65,62M2 Mieszkani... NaN   

                                                  24  
0  telewizja kablowa, internet, telefon, domofon ...  
1                                             balkon  
2  telewizja kablowa, internet, telefon, piwnica,...  
3  telewizja kablowa, internet, telefon, drzwi / ...  
4     garaż/miejsce parkingowe, taras, pom. użytkowe

In [219]:
y_test = pd.read_csv('expected.tsv', sep='\t', header=None)

In [220]:
X_train

stan  l pokoi  metraż      rynek
0     do zamieszkania        2   43.44     wtórny
1      do wykończenia        2   42.60  pierwotny
2          do remontu        2   44.30     wtórny
3     do zamieszkania        4   88.00     wtórny
4           brak info        3   77.00     wtórny
...               ...      ...     ...        ...
2541   do wykończenia        3   70.40  pierwotny
2542   do wykończenia        4   94.00     wtórny
2543        brak info        2   53.50     wtórny
2544        brak info        3   55.25     wtórny
2545        brak info        3   62.00     wtórny

[2540 rows x 4 columns]

In [221]:
df_test.rename(columns={0: "stan", 1: "czynsz", 5: "l pokoi", 7: "metraż", 8: "rynek"}, inplace=True)

In [222]:
df_test.columns

Index([   'stan',  'czynsz',         2,         3,         4, 'l pokoi',
               6,  'metraż',   'rynek',         9,        10,        11,
              12,        13,        14,        15,        16,        17,
              18,        19,        20,        21,        22,        23,
              24],
      dtype='object')

In [223]:
df_test = df_test[['stan', 'l pokoi', 'metraż',  'rynek']] 

In [224]:
df_test.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 462 entries, 0 to 461
Data columns (total 4 columns):
 #   Column   Non-Null Count  Dtype  
---  ------   --------------  -----  
 0   stan     275 non-null    object 
 1   l pokoi  462 non-null    int64  
 2   metraż   462 non-null    float64
 3   rynek    462 non-null    object 
dtypes: float64(1), int64(1), object(2)
memory usage: 14.6+ KB


In [225]:
df_test['stan'].fillna('brak info', inplace=True)

In [226]:
df_test.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 462 entries, 0 to 461
Data columns (total 4 columns):
 #   Column   Non-Null Count  Dtype  
---  ------   --------------  -----  
 0   stan     462 non-null    object 
 1   l pokoi  462 non-null    int64  
 2   metraż   462 non-null    float64
 3   rynek    462 non-null    object 
dtypes: float64(1), int64(1), object(2)
memory usage: 14.6+ KB


In [227]:
df_test['metraż']

0      59.10
1      38.00
2      63.84
3      50.00
4      65.62
       ...  
457    72.78
458    51.23
459    54.16
460    90.10
461    71.90
Name: metraż, Length: 462, dtype: float64

In [228]:
df_test.reset_index(drop=True, inplace=True)

In [229]:
df_test.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 462 entries, 0 to 461
Data columns (total 4 columns):
 #   Column   Non-Null Count  Dtype  
---  ------   --------------  -----  
 0   stan     462 non-null    object 
 1   l pokoi  462 non-null    int64  
 2   metraż   462 non-null    float64
 3   rynek    462 non-null    object 
dtypes: float64(1), int64(1), object(2)
memory usage: 14.6+ KB


In [230]:
model1

Pipeline(steps=[('columntransformer',
                 ColumnTransformer(transformers=[('num',
                                                  Pipeline(steps=[('standardscaler',
                                                                   StandardScaler())]),
                                                  Index(['l pokoi', 'metraż'], dtype='object')),
                                                 ('cat',
                                                  Pipeline(steps=[('onehotencoder',
                                                                   OneHotEncoder())]),
                                                  Index(['stan', 'rynek'], dtype='object'))])),
                ('ridge', Ridge())])

Przykład - przewidywanie cen na danych testowych

In [231]:
model1.predict(df_test)

array([ 407917.66889452,  285306.27863261,  444184.94702291,
        299459.05926666,  459271.83408962,  614055.95902743,
        311243.98561031,  361244.58944658,  329238.65906305,
        369470.84812889,  285350.13919824,  329238.65906305,
        420020.53940636,  399085.99304054,  368717.32379097,
        339834.65864991,  335512.74515277,  304524.88092914,
        367036.20209137,  286773.80808993,  354525.20168926,
        282085.35025252,  386303.76202814,  477660.29347794,
        407152.53644455,  490742.17175818,  529758.94244497,
        335044.40697838,  399501.21194489,  431641.29394143,
        331214.22563058,  334772.89329194,  404282.20491201,
        369968.98599038,  392538.22357404,  354476.13872373,
        531690.53563375,  428309.25045513,  298510.41733766,
        551966.54555785,  332974.0302655 ,  474293.99377424,
        247049.65613431,  383931.85143325,  546789.20856336,
        438766.28443053,  275556.44383868,  325403.7381088 ,
        319934.12593671,

Saving the model to file

In [233]:
filename = 'ridge_model.sav'
joblib.dump(model1, filename)

['ridge_model.sav']